In [1]:
import pandas as pd 

/Users/martinmaele/opt/anaconda3/lib/python3.9/site-packages/pandas/core/computation/expressions.py:21: UserWarning: Pandas requires version '2.8.4' or newer of 'numexpr' (version '2.7.3' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED
/Users/martinmaele/opt/anaconda3/lib/python3.9/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.2' currently installed).
  from pandas.core import (


In [2]:
train = pd.read_csv('ais_train.csv', sep='|') 
train['time'] = pd.to_datetime(train['time']) 
vessel1 =train[train['vesselId'] == '61e9f3f2b937134a3c4bff9d'] 
train.tail() 

time    cog   sog  rot  heading  navstat       etaRaw  \
1522060 2024-05-07 23:59:07  359.1  13.4    0        1        0  05-08 05:00   
1522061 2024-05-07 23:59:08   12.3  17.1    0       13        0  05-10 03:00   
1522062 2024-05-07 23:59:08  269.8  14.9   -1      270        0  05-15 23:00   
1522063 2024-05-07 23:59:08    8.0  18.7    0        6        0  05-08 12:45   
1522064 2024-05-07 23:59:08  336.0  14.3    5      337        0  05-07 23:00   

         latitude  longitude                   vesselId  \
1522060  52.19131   -5.82223  clh6aqawa0002gh0zypfa5dut   
1522061  38.96142  -12.00502   61e9f3aeb937134a3c4bfe43   
1522062  49.71372   -5.22042   61e9f43db937134a3c4c0169   
1522063  38.27895   10.78280   61e9f469b937134a3c4c029b   
1522064  38.98635  -75.13275   62080cff66fc0a8e43c6123a   

                           portId  
1522060  634c4de270937fc01c3a7417  
1522061  634c4de270937fc01c3a76a1  
1522062  634c4de270937fc01c3a787b  
1522063  61d3781293c6feb83e5eb73b  
1522064  61d38528b7b7526e1adf3e6f

In [3]:
train.describe()

time           cog           sog  \
count                        1522065  1.522065e+06  1.522065e+06   
mean   2024-03-06 03:20:23.657231360  1.782494e+02  6.331703e+00   
min              2024-01-01 00:00:25  0.000000e+00  0.000000e+00   
25%              2024-02-03 02:59:19  7.820000e+01  0.000000e+00   
50%              2024-03-07 12:34:57  1.838000e+02  5.000000e-01   
75%              2024-04-07 07:37:36  2.690000e+02  1.410000e+01   
max              2024-05-07 23:59:08  3.600000e+02  1.023000e+02   
std                              NaN  1.076785e+02  7.539364e+00   

                rot       heading       navstat      latitude     longitude  
count  1.522065e+06  1.522065e+06  1.522065e+06  1.522065e+06  1.522065e+06  
mean   5.054561e-01  1.762737e+02  2.092604e+00  3.658497e+01  1.153646e+01  
min   -1.270000e+02  0.000000e+00  0.000000e+00 -4.753287e+01 -1.675409e+02  
25%    0.000000e+00  7.500000e+01  0.000000e+00  3.451683e+01 -5.212810e+00  
50%    0.000000e+00  1.800000e+02  0.000000e+00  4.223370e+01  4.234350e+00  
75%    0.000000e+00  2.650000e+02  5.000000e+00  5.135197e+01  1.883715e+01  
max    1.280000e+02  5.110000e+02  1.500000e+01  7.055720e+01  1.788054e+02  
std    1.760916e+01  1.070860e+02  2.411965e+00  2.290488e+01  6.871572e+01

In [4]:
# Description of entries per vessel
counts = train.groupby(["vesselId"]).count()
print(counts["time"].describe()) 

count     688.000000
mean     2212.303779
std      1659.631687
min         1.000000
25%      1141.750000
50%      1709.000000
75%      2482.000000
max      8656.000000
Name: time, dtype: float64


In [5]:
#cog = train.groupby([""]) 
# Det jeg vil se på er hvordan forskjellige features henger sammen med posisjonen fremover i tid. FØrst må jeg forstå bedre hvordan jeg akn gjøre dette



In [6]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

def visualize_vessel_movements(df):
    """
    Visualize vessel movements on a map with lines and markers for each data point.

    Parameters:
    - df (pandas.DataFrame): A DataFrame with columns ['time', 'latitude', 'longitude', 'vesselId'].

    Returns:
    - A Plotly interactive figure.
    """
    # Ensure 'time' is in datetime format for better tooltip handling
    df['time'] = pd.to_datetime(df['time'])
    
    # Sorting the DataFrame by time to ensure lines are drawn correctly
    df = df.sort_values(by=['vesselId', 'time'])

    # Define a color palette
    color_map = px.colors.qualitative.Plotly

    # Mapping each vessel ID to a color
    unique_vessels = df['vesselId'].unique()
    colors = {vessel_id: color_map[i % len(color_map)] for i, vessel_id in enumerate(unique_vessels)}

    # Create the base map with lines
    fig = px.line_geo(df,
                      lat='latitude',
                      lon='longitude',
                      color='vesselId',
                      color_discrete_map=colors,
                      hover_name='vesselId',
                      hover_data={'time': True, 'latitude': ':.3f', 'longitude': ':.3f'},
                      projection='natural earth',
                      title='Vessel Movements Over Time')

    # Add markers for each data point
    for vessel_id in unique_vessels:
        vessel_data = df[df['vesselId'] == vessel_id]
        fig.add_trace(go.Scattergeo(
            lon=vessel_data['longitude'],
            lat=vessel_data['latitude'],
            mode='markers',
            marker=dict(
                size=8,
                color=colors[vessel_id],
                opacity=0.8,
                line=dict(width=1, color='DarkSlateGrey')
            ),
            name=f'Markers for {vessel_id}',
            hoverinfo='text',
            text=vessel_data.apply(lambda row: f'ID: {vessel_id}<br>Time: {row["time"]}<br>Lat: {row["latitude"]:.3f}<br>Lon: {row["longitude"]:.3f}', axis=1)
        ))

    # Enhancing map and layout details
    fig.update_geos(fitbounds="locations", showcountries=True, countrycolor="RebeccaPurple")
    fig.update_layout(margin={"r":0,"t":30,"l":0,"b":0},
                      coloraxis_colorbar=dict(title="Vessel ID"),
                      title_font_size=20)
    
    return fig

fig = visualize_vessel_movements(
    train[train['vesselId'] == '61e9f3a8b937134a3c4bfdf7']
)
fig.show() 



/var/folders/8g/d2wk3x0d7jz2_0srl03y6_mm0000gn/T/ipykernel_9052/3092577748.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['time'] = pd.to_datetime(df['time'])


In [7]:
print(train[train['vesselId'] == '61e9f3a8b937134a3c4bfdf7'].to_string())

# konklusjoner etter studering av 'vesselId'] == '61e9f3a8b937134a3c4bfdf7'
# Hvis fart (SOG) er høy +8 er det lite endring i Course over ground (COG) fra måling til måling.
# Samme gjelder hvis SOG er 0. Antar båten står stille. 
# For skipet under er det noe galt med ROT målingene. DE er ikke informative
# Heading er stort sett veldig lik COG. Men noen ganger bare helt fulsltendig off (vurderingssak å kutte denne hvis det viser seg at den er off andre steder også. Gir dermed potensielt lite)
# PortID kan forskes litt på. Er det noen av disse portene som typisk har kryssatlantiske skip. Må de modeleres på andre måter enn middelhavsbåtene
# Home port Har vistok rammifications for compliance, skatt og operasjonell logistikk. 
# yearbuilt. Har rammifactions for effektivitet, regulatorisk compliance, vedlikehold. 
# bedre enn ingenting å ta snittet av forrige og neste ved manglende COG verdi. Dersom det er mer enn 
# et mål kan være if samme dag foran og bak: gj snitt 
# If ikke samme dag, men foran < 0.1 or > 10.0 
# gj snitt. Samme foran og bak 
# Else. set COG lik målingen som er nærmest 
# ETARAW er jo en kul metrikkel. Den må brukes for det den er verdt. Kombinere med portlocations Ev PortID kan være en idé. Ellers må vi se på h

# Vessel 
# Gross tonnage (GT) har dette noe med turningrate å gjøre? Kankje ikke så viktig mtp at skipene turner mest i havnene når de står helt i ro
# Net tonnage (NT) kan være mer interresant når det skal lages et mål på hvor lenge et skip må loke inne i havnen. Hvor lang tid tar det å shippe av/på. Dette kan jeg lese på (er det 2 dager eller 2 timer)
# Breadth: ?  
# Vessel lenght er possibly determinativt for hvorvidt det er snakk om deep-sea eller short sea ship. Kan potensielt modelere disse forskjellig. Tenke på det 

# Schedule 
# Schedule er også en veldig interresant klasse. Her er det både 
# arrival date, departure date er knask 
# En ting vi kan gjøre er å bare ta Schedule i betraktning hvis skipet seiler på den opplagte ruten. Vet ikke hvordan. men verdt å se på. 
# En model for skip på schedule og et for de som ikke. 

# Navstat 0 - under way sailing. Kan være interresant om det er flere båter som har andre NAVSTAT og må behandles på egen måte. Er det feks en type båter som bare ligger og loker til reparasjon etc. går dårlig 
# Kanskje lurt å ha med navstat som en feature siden 
# HEr er feks kordinatene helt like over tid når navstat = 1 samme med navstat = 5 
# Se på dette 
# 0	Under way using engine - Seiling 
# 1	At anchor - stand still 
# 2	Not under command 
# 3	Restricted manoeuverability 
# 4	Constrained by her draught 
# 5	Moored - stand still 
# 6	Aground 
# 7	Engaged in Fishing - vet ikke 
# 8	Under way sailing - Seiling 



                       time    cog   sog  rot  heading  navstat       etaRaw  latitude  longitude                  vesselId                    portId
0       2024-01-01 00:00:25  284.0   0.7    0       88        0  01-09 23:00 -34.74370  -57.85130  61e9f3a8b937134a3c4bfdf7  61d371c43aeaecc07011a37f
2672    2024-01-01 06:09:08   92.8  14.2    0       90        0  01-09 23:00 -35.16787  -56.77210  61e9f3a8b937134a3c4bfdf7  61d371c43aeaecc07011a37f
2947    2024-01-01 06:38:19   90.5  14.3    0       88        0  01-09 23:00 -35.16863  -56.63185  61e9f3a8b937134a3c4bfdf7  61d371c43aeaecc07011a37f
3093    2024-01-01 06:58:55   88.2  14.3    0       86        0  01-09 23:00 -35.16805  -56.53190  61e9f3a8b937134a3c4bfdf7  61d371c43aeaecc07011a37f
3140    2024-01-01 07:15:56   88.3  12.3    0       86        0  01-09 23:00 -35.16715  -56.45306  61e9f3a8b937134a3c4bfdf7  61d371c43aeaecc07011a37f
3280    2024-01-01 07:28:15   86.8  11.7    0       85        0  01-09 23:00 -35.16646  -56.40306  6

In [8]:
print(train[train['vesselId'] == '61e9f3c7b937134a3c4bfedd'].to_string()) 



                       time    cog    sog  rot  heading  navstat       etaRaw  latitude  longitude                  vesselId                    portId
259696  2024-01-23 20:52:13    0.0   14.2    5        0        0  12-20 08:00  17.46174  -17.96609  61e9f3c7b937134a3c4bfedd  61d37ede29b60f6113c89cf9
281066  2024-01-25 16:51:46   38.0   13.7    0       38        0  12-20 08:00  27.07269  -14.55627  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281289  2024-01-25 17:14:20  360.0  102.3  -17       38        0  12-20 08:00  27.14130  -14.49507  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281521  2024-01-25 17:35:19   38.2   14.2    0       36        0  02-01 11:00  27.20500  -14.43613  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281621  2024-01-25 17:55:08   37.6   14.2   16       34        0  02-01 11:00  27.26794  -14.38323  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281799  2024-01-25 18:15:50   38.8   14.4   12       36        0  02-01 11:00  27.33252  -14.3

In [9]:
# give me a dataframe with all the rows in train where 'cog'= 360.0 and 'navstat'= 0
# Write code here
# Create a new dataframe where for each row in cog_360 include the subsequent 3 rows and the previous 3 rows where the 'vesselId' is the same as in the row in cog_360.


#print(cog_360.to_string())
#print(len(cog_360))

new_train = train.copy()

# For new train if 'cog' == 360.0 and ('navstat' == 1 or 'navstat' == 5) change the 'cog' value to 0.0 

#new_train.loc[(new_train['cog'] == 360.0) & ((new_train['navstat'] == 1) | (new_train['navstat'] == 5)), 'cog'] = 0.0 

#Create a new dataframe where made from train with an extra column named vessels_entry which is an index for each individual vessel corresponding to the order in which each entry for the vessel is recorded. Thus each vessel will have entries numbered 0, 1, 2, 3, ...

#new_train['vessels_entry'] = new_train.groupby('vesselId').cumcount()



# give me a dataframe with all the rows in train where 'cog'= 360.0 and 'navstat'= 1 or 'navstat'= 5 made from new_train

cog_360 = new_train[(new_train['cog'] == 360.0) & ((new_train['navstat'] == 1) | (new_train['navstat'] == 5))]
cog_360 = new_train[(new_train['cog'] == 360.0) & ((new_train['navstat'] == 0))] 

#print(cog_360.to_string())

#For new_train, if 'cog' == 360.0 and 'navstat' == 0 change the 'cog' value to the mean of the 'cog' value vessel_entry -1 and vessel_entry + 1 and 'vesselId' is the same. 

# Write code here please 

# Create a list of all unique vesselIds in new_train

vesselIds = new_train['vesselId'].unique()
#for vesselId in vesselIds:
#    vessel = new_train[new_train['vesselId'] == vesselId]
#    vessel.reset_index(inplace=True)
#    cog_360 = vessel[(vessel['cog'] == 360.0)]
#    if (len(cog_360) == 0): 
#        continue 
#    for index, row in cog_360.iterrows(): 
#        if index == 0:
#            while vessel.loc[index, 'cog'] == 360.0: 
#                index += 1 
#            vessel.loc[0, 'cog'] = vessel.loc[index, 'cog']
#            continue
#        prevIndex = index - 1
#        while vessel.loc[prevIndex, 'cog'] == 360.0: 
#            prevIndex -= 1
#        subsequentIndex = index
#        while vessel.loc[index, 'cog'] == 360.0:
#            subsequentIndex += 1
#        vessel.loc[index, 'cog'] = (vessel.loc[prevIndex, 'cog'] + vessel.loc[subsequentIndex, 'cog']) / 2.0 
#    new_train.loc[new_train['vesselId'] == vesselId, 'cog'] = vessel['cog'] 
import numpy as np
for vesselId in vesselIds:
#for vesselId in ['61e9f3c7b937134a3c4bfedd']:
    vessel = new_train[new_train['vesselId'] == vesselId].copy()
    vessel['cog'] = vessel['cog'].replace(360.0, np.nan)
    vessel['cog'].interpolate(method='linear', inplace=True)
    vessel['cog'].ffill(inplace=True) 
    vessel['cog'].bfill(inplace=True) 
    new_train.loc[new_train['vesselId'] == vesselId, 'cog'] = vessel['cog']

print(new_train[new_train['vesselId'] == '61e9f3c7b937134a3c4bfedd'].to_string()) 
print(len(new_train[(new_train['cog'] == 360.0)])) 

#Create a new dataframe where made from train with an extra column named vessels_entry which is an index for each individual vessel corresponding to the order in which each entry for the vessel is recorded. Thus each vessel will have entries numbered 0, 1, 2, 3, ... 

#print(new_train[new_train['vesselId'] == '61e9f3c7b937134a3c4bfedd'].to_string())

/var/folders/8g/d2wk3x0d7jz2_0srl03y6_mm0000gn/T/ipykernel_9052/2810520697.py:60: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.



/var/folders/8g/d2wk3x0d7jz2_0srl03y6_mm0000gn/T/ipykernel_9052/2810520697.py:61: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing '

                       time         cog    sog  rot  heading  navstat       etaRaw  latitude  longitude                  vesselId                    portId
259696  2024-01-23 20:52:13    0.000000   14.2    5        0        0  12-20 08:00  17.46174  -17.96609  61e9f3c7b937134a3c4bfedd  61d37ede29b60f6113c89cf9
281066  2024-01-25 16:51:46   38.000000   13.7    0       38        0  12-20 08:00  27.07269  -14.55627  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281289  2024-01-25 17:14:20   38.100000  102.3  -17       38        0  12-20 08:00  27.14130  -14.49507  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281521  2024-01-25 17:35:19   38.200000   14.2    0       36        0  02-01 11:00  27.20500  -14.43613  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281621  2024-01-25 17:55:08   37.600000   14.2   16       34        0  02-01 11:00  27.26794  -14.38323  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281799  2024-01-25 18:15:50   38.800000   14.4   12       36    

In [10]:
for vesselId in vesselIds: 
#for vesselId in ['61e9f3c7b937134a3c4bfedd']:
    vessel = new_train[new_train['vesselId'] == vesselId].copy()
    vessel['sog'] = vessel['sog'].replace(102.3, np.nan)
    # replace 'soc' values above 28.0 with nan 
    vessel.loc[vessel['sog'] > 30.0] = np.nan
    vessel['sog'].interpolate(method='linear', inplace=True)
    vessel['sog'].ffill(inplace=True)
    vessel['sog'].bfill(inplace=True)
    new_train.loc[new_train['vesselId'] == vesselId, 'sog'] = vessel['sog'] 

print(new_train[new_train['vesselId'] == '61e9f3c7b937134a3c4bfedd'].to_string()) 
print(len(new_train[(new_train['sog'] == 360.0)])) 

/var/folders/8g/d2wk3x0d7jz2_0srl03y6_mm0000gn/T/ipykernel_9052/3557392148.py:7: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.



/var/folders/8g/d2wk3x0d7jz2_0srl03y6_mm0000gn/T/ipykernel_9052/3557392148.py:8: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df

                       time         cog        sog  rot  heading  navstat       etaRaw  latitude  longitude                  vesselId                    portId
259696  2024-01-23 20:52:13    0.000000  14.200000    5        0        0  12-20 08:00  17.46174  -17.96609  61e9f3c7b937134a3c4bfedd  61d37ede29b60f6113c89cf9
281066  2024-01-25 16:51:46   38.000000  13.700000    0       38        0  12-20 08:00  27.07269  -14.55627  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281289  2024-01-25 17:14:20   38.100000  13.950000  -17       38        0  12-20 08:00  27.14130  -14.49507  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281521  2024-01-25 17:35:19   38.200000  14.200000    0       36        0  02-01 11:00  27.20500  -14.43613  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281621  2024-01-25 17:55:08   37.600000  14.200000   16       34        0  02-01 11:00  27.26794  -14.38323  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281799  2024-01-25 18:15:50   38.800000 

In [11]:
for vesselId in vesselIds: 
#for vesselId in ['61e9f3c7b937134a3c4bfedd']:
    vessel = new_train[new_train['vesselId'] == vesselId].copy()
    vessel.loc[vessel['rot'] == 128] = np.nan
    vessel['rot'].interpolate(method='linear', inplace=True)
    vessel['rot'].ffill(inplace=True)
    vessel['rot'].bfill(inplace=True)
    new_train.loc[new_train['vesselId'] == vesselId, 'rot'] = vessel['rot']

vessel.loc[vessel['rot'] == np.nan] = 0 
print(new_train[new_train['vesselId'] == '61e9f3c7b937134a3c4bfedd'].to_string()) 
print(len(new_train[(new_train['rot'] == 128)])) 

/var/folders/8g/d2wk3x0d7jz2_0srl03y6_mm0000gn/T/ipykernel_9052/3772357414.py:5: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.



/var/folders/8g/d2wk3x0d7jz2_0srl03y6_mm0000gn/T/ipykernel_9052/3772357414.py:6: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df

                       time         cog        sog   rot  heading  navstat       etaRaw  latitude  longitude                  vesselId                    portId
259696  2024-01-23 20:52:13    0.000000  14.200000   5.0        0        0  12-20 08:00  17.46174  -17.96609  61e9f3c7b937134a3c4bfedd  61d37ede29b60f6113c89cf9
281066  2024-01-25 16:51:46   38.000000  13.700000   0.0       38        0  12-20 08:00  27.07269  -14.55627  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281289  2024-01-25 17:14:20   38.100000  13.950000 -17.0       38        0  12-20 08:00  27.14130  -14.49507  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281521  2024-01-25 17:35:19   38.200000  14.200000   0.0       36        0  02-01 11:00  27.20500  -14.43613  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281621  2024-01-25 17:55:08   37.600000  14.200000  16.0       34        0  02-01 11:00  27.26794  -14.38323  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281799  2024-01-25 18:15:50   38.8

In [12]:
print(len(new_train[(new_train['rot'] == 128)])) 

0


In [13]:
# I want heading to be changed to be equal to cog if heading is > 360.0 

new_train.loc[new_train['heading'] > 360.0, 'heading'] = new_train.loc[new_train['heading'] > 360.0, 'cog']

/var/folders/8g/d2wk3x0d7jz2_0srl03y6_mm0000gn/T/ipykernel_9052/1636430003.py:3: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[123.4 123.4 123.4 ...   4.  347.  347. ]' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.



In [14]:
print(new_train[new_train['vesselId'] == '61e9f3c7b937134a3c4bfedd'].to_string()) 

print(len(new_train[(new_train['cog'] == 360.0)])) 
print(len(train[(train['cog'] == 360.0)])) 

                       time         cog        sog   rot  heading  navstat       etaRaw  latitude  longitude                  vesselId                    portId
259696  2024-01-23 20:52:13    0.000000  14.200000   5.0      0.0        0  12-20 08:00  17.46174  -17.96609  61e9f3c7b937134a3c4bfedd  61d37ede29b60f6113c89cf9
281066  2024-01-25 16:51:46   38.000000  13.700000   0.0     38.0        0  12-20 08:00  27.07269  -14.55627  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281289  2024-01-25 17:14:20   38.100000  13.950000 -17.0     38.0        0  12-20 08:00  27.14130  -14.49507  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281521  2024-01-25 17:35:19   38.200000  14.200000   0.0     36.0        0  02-01 11:00  27.20500  -14.43613  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281621  2024-01-25 17:55:08   37.600000  14.200000  16.0     34.0        0  02-01 11:00  27.26794  -14.38323  61e9f3c7b937134a3c4bfedd  634c4de270937fc01c3a74ef
281799  2024-01-25 18:15:50   38.8

In [15]:
schedule = pd.read_csv('schedules_to_may_2024.csv', sep='|') 
print(schedule[schedule['vesselId'] == '61e9f3a8b937134a3c4bfdf7'].to_string())

print(schedule[schedule['vesselId'] == '61e9f39eb937134a3c4bfdcb'].to_string())
# conditional on the previous and subsequent 'cog' value being different from 360.0 and the 'time' value being within one hour of the 'time' value of the row at hand. 

# Write code here


## For all instances where 'cog' is still == 360 please input the value from the that has the same 'vesselId' and the closest 'time' value.
## Write code here: 

Empty DataFrame
Columns: [vesselId, shippingLineId, shippingLineName, arrivalDate, sailingDate, portName, portId, portLatitude, portLongitude]
Index: []
                        vesselId            shippingLineId shippingLineName                arrivalDate                sailingDate                  portName                    portId  portLatitude  portLongitude
1430    61e9f39eb937134a3c4bfdcb  61a8e673f9cba188601e84ae           K-Line  2023-10-14 00:00:00+00:00  2023-10-14 00:00:00+00:00         Port of Baltimore  61d3847bb7b7526e1adf3d19     39.232500     -76.558889
1431    61e9f39eb937134a3c4bfdcb  61a8e673f9cba188601e84ae           K-Line  2023-10-18 00:00:00+00:00  2023-10-19 00:00:00+00:00           Port Charleston  61d3847cb7b7526e1adf3d1b     32.822222     -79.927500
1432    61e9f39eb937134a3c4bfdcb  61a8e673f9cba188601e84ae           K-Line  2023-10-16 00:00:00+00:00  2023-10-17 00:00:00+00:00         Port of Brunswick  61d38499b7b7526e1adf3d54     31.140556     -81.496667
143

In [16]:
print(schedule[schedule['vesselId'] == "61e9f3f4b937134a3c4bffb5"].to_string())

                        vesselId            shippingLineId            shippingLineName                arrivalDate                sailingDate             portName                    portId  portLatitude  portLongitude
358     61e9f3f4b937134a3c4bffb5  61a8e672f9cba188601e84ac  Wallenius Wilhelmsen Ocean  2024-05-31 00:00:00+00:00  2024-05-31 00:00:00+00:00      Port of Halifax  61d3705e0a1807568ff9a1f1     44.656944     -63.578889
359     61e9f3f4b937134a3c4bffb5  61a8e672f9cba188601e84ac  Wallenius Wilhelmsen Ocean  2024-06-06 00:00:00+00:00  2024-06-06 00:00:00+00:00    Port of Brunswick  61d38499b7b7526e1adf3d54     31.140556     -81.496667
360     61e9f3f4b937134a3c4bffb5  61a8e672f9cba188601e84ac  Wallenius Wilhelmsen Ocean  2024-05-19 00:00:00+00:00  2024-05-20 00:00:00+00:00  Port of Bremerhaven  61d375e793c6feb83e5eb3e2     53.563611       8.554722
361     61e9f3f4b937134a3c4bffb5  61a8e672f9cba188601e84ac  Wallenius Wilhelmsen Ocean  2024-06-02 00:00:00+00:00  2024-06-03 00:00:

In [17]:
print(schedule[schedule['vesselId'] == "61e9f3a7b937134a3c4bfdeb"].to_string())


                        vesselId            shippingLineId            shippingLineName                arrivalDate                sailingDate                      portName                    portId  portLatitude  portLongitude
586     61e9f3a7b937134a3c4bfdeb  61a8e672f9cba188601e84ab            Hoegh Autoliners  2024-02-18 03:00:00+00:00  2024-02-18 22:00:00+00:00                Port of Mumbai  61d376d893c6feb83e5eb546     18.941944      72.885278
587     61e9f3a7b937134a3c4bfdeb  61a8e672f9cba188601e84ab            Hoegh Autoliners  2024-02-07 03:00:00+00:00  2024-02-10 14:00:00+00:00                           NaN                       NaN           NaN            NaN
588     61e9f3a7b937134a3c4bfdeb  61a8e672f9cba188601e84ab            Hoegh Autoliners  2024-02-11 03:00:00+00:00  2024-02-11 22:00:00+00:00            Port of Port Louis  61d37a981366c3998241d9d9    -20.148056      57.493611
589     61e9f3a7b937134a3c4bfdeb  61a8e672f9cba188601e84ab            Hoegh Autoliners  2024-01-

In [18]:
print(schedule[schedule['vesselId'] == "61e9f412b937134a3c4c0051"].to_string())

                        vesselId            shippingLineId shippingLineName                arrivalDate                sailingDate                  portName                    portId  portLatitude  portLongitude
1726    61e9f412b937134a3c4c0051  61a8e673f9cba188601e84b3             UECC  2024-03-31 02:12:00+00:00  2024-03-31 19:00:00+00:00              Port of Vigo  61d37fbc29b60f6113c89ea6     42.242500      -8.731667
1727    61e9f412b937134a3c4c0051  61a8e673f9cba188601e84b3             UECC  2024-03-09 02:00:00+00:00  2024-03-10 08:00:00+00:00            Port of Maputo  61d37ad61366c3998241da24    -25.972778      32.561111
1728    61e9f412b937134a3c4c0051  61a8e673f9cba188601e84b3             UECC  2024-05-09 14:00:00+00:00  2024-05-09 20:00:00+00:00           Port of Sagunto  61d37fb629b60f6113c89e99     39.642778      -0.212500
1729    61e9f412b937134a3c4c0051  61a8e673f9cba188601e84b3             UECC  2024-03-24 11:24:00+00:00  2024-03-25 21:00:00+00:00                       NaN 

Vi har ganske mye data her fra 2023. VI kunne prøvd å få et intrykk av hvor korrekt den dataen var ved å sammenligne med faktiske ruter. 

Er det helt fullstendig villspor så bruker vi ikke mer tid her 

Er det feks slik at en liten forsinkelse i en havn gjør at båten kommer frem til feil tid på alle senere havnebesøk

Interresant å se på i tilfelle. 

Kanskje er det mulig å gjøre noe kondisjonelt her. Bare hente data herfra hvis båten er on track? 
Drite i tidsaspektet kanskje og bare se på om båten er underveis på en satt rute. 

Se på å sammenligne med ETARAW (er dette egnetlig akkurat det samme som schedule?) I såfall får vi ikke så mye mer informasjon. 

Innlevering
Hvilke timestamps skal vi sample på? 



In [19]:
# Use the schedule dataframe to create a new dataframe called ports. In the dataframe ports i want you to have one row for each port and the columns should be the portId, the port name, the country and the coordinates of the port.
# The coordinates should be in two columns, one for latitude and one for longitude.

ports = schedule[['portName','portId','portLatitude','portLongitude']].drop_duplicates()
print(ports.to_string()) 

                                 portName                    portId  portLatitude  portLongitude
0                       Port of Brunswick  61d38499b7b7526e1adf3d54     31.140556     -81.496667
1                     Port of Southampton  61d3832bb7b7526e1adf3b63     50.902500      -1.428889
2                     Port of Bremerhaven  61d375e793c6feb83e5eb3e2     53.563611       8.554722
3                        Port of New York  61d38481b7b7526e1adf3d23     40.688333     -74.028611
4       Manzanillo International Terminal  61d37d0199db2ccf7339eee1      9.372370     -79.879790
5                        Port of Savannah  61d38483b7b7526e1adf3d27     32.110833     -81.125833
6                       Port of Baltimore  61d3847bb7b7526e1adf3d19     39.232500     -76.558889
7                Port of Bruges-Zeebrugge  61d36f9a0a1807568ff9a156     51.336389       3.207222
8                          Port of Durban  61d37ef929b60f6113c89d1b    -29.881111      31.027222
9                           Po

In [20]:
# please create a dataframe containing only the first 200.000 rows of the ais_train dataframe.
train2 = train.head(100)

In [21]:
# can you find all rows where sog is 102.2 knots or less and and larger than 70.0 knots?

print(train[(train['sog'] <= 102.2) & (train['sog'] > 25.0)].to_string()) 

                       time    cog    sog  rot  heading  navstat       etaRaw  latitude  longitude                  vesselId                    portId
13578   2024-01-02 04:37:25  302.7   32.0    0      289        0  12-30 19:00  51.88025    4.42176  61e9f414b937134a3c4c005f  61d37be499db2ccf7339ecc5
60422   2024-01-06 05:00:44  196.3   32.0    2       21        0  01-29 06:00  49.18052 -122.91846  61e9f400b937134a3c4bfffb  61d3744f3aeaecc07011a719
64857   2024-01-06 13:59:58   84.9   25.4    0       84        0  01-05 22:30  42.99495    7.73797  61e9f469b937134a3c4c029f  61d3781293c6feb83e5eb73b
66525   2024-01-06 17:38:42  150.3   25.1    0      151        0  01-05 22:30  42.92066    9.63708  61e9f469b937134a3c4c029f  61d3781293c6feb83e5eb73b
86463   2024-01-08 14:58:15   48.3   32.0    0      105        0  12-25 12:00  51.89046    4.45849  61e9f466b937134a3c4c0273  61d37be499db2ccf7339ecc5
92840   2024-01-09 04:23:10  207.3   32.0   67      162        0  01-01 18:00  52.40765    4.8

In [22]:
# Now i want you to create a new dataframe where the ports and train dataframes are merged together. A row from the schedules dataframe should be merged with a row from the train dataframe if the latitude and longitude in train is withing 3 nautical miles of the portLatitude and portLongitude in the ports dataframe.

# The new dataframe should have the following columns: vesselId, time, portId, portName, country, portLatitude, portLongitude, latitude, longitude

# The new dataframe should be sorted by vesselId and time.


import numpy as np
from math import radians, sin, cos, sqrt, atan2

#def haversine_distance(lat1, lon1, lat2, lon2):
#    # Calculate the haversine distance between two points in latitude and longitude
#    R = 6371.0  # Radius of the Earth in km
#    lat1, lon1, lat2, lon2 = map(radians, [lat1, lon1, lat2, lon2])
#    dlat = lat2 - lat1
#    dlon = lon2 - lon1
#    a = sin(dlat / 2)**2 + cos(lat1) * cos(lat2) * sin(dlon / 2)**2
#    c = 2 * atan2(sqrt(a), sqrt(1 - a))
#    return R * c
#
#def merge_ports_and_train(ports, train):
#    # Merge the ports and train dataframes
#    # A row from the schedules dataframe should be merged with a row from the train dataframe if the latitude and longitude in train is withing 3 nautical miles of the portLatitude and portLongitude in the ports dataframe. 
#    # Write code
#    # AttributeError: 'DataFrame' object has no attribute 'append'
#    
#    merged_df = pd.DataFrame(columns=['vesselId', 'time', 'portId', 'portName', 'country', 'portLatitude', 'portLongitude', 'latitude', 'longitude'])
#    for index, row in ports.iterrows():
#        for index2, row2 in train.iterrows():
#            if haversine_distance(row['portLatitude'], row['portLongitude'], row2['latitude'], row2['longitude']) < 3:
#                row['vesselId'] = row2['vesselId']
#                row['time'] = row2['time']
#                row['latitude'] = row2['latitude']
#                row['longitude'] = row2['longitude']
#                merged_df = merged_df._append(row, ignore_index=True)
#    return merged_df  
#
#
#merged_df = merge_ports_and_train(ports, train2)
#print(merged_df.to_string()) 

In [23]:
# Load the dataframe ais_test.csv into a dataframe called test
test = pd.read_csv('ais_test.csv', sep=',')

test2 = test.copy()

vessels_in_train = train['vesselId'].unique()
print(len(vessels_in_train))

vessels_in_test = test2['vesselId'].unique()
print(len(vessels_in_test))
# Can you find how many of the vessels contained in test are contained in train?

vessels_in_both = np.intersect1d(vessels_in_test, ['61e9f461b937134a3c4c024d'])
print(len(vessels_in_both)) 



688
215
1


In [24]:
otherNavstats = train[~train['navstat'].isin([0, 1, 5, 8])]
print(otherNavstats.to_string())

navstat15 = new_train[new_train['navstat'].isin([15])]
#print(navstat15.to_string())

# Can you change the rows where 'navstat' == 15 to have 'navstat' == 0 if the 'sog' is strictly larger than 0.1. And change the rows where 'navstat' == 15 to have 'navstat' == 1 if the 'sog' is 0.0 or 0.1.

new_train.loc[(new_train['navstat'] == 15) & (new_train['sog'] > 0.1), 'navstat'] = 0
new_train.loc[(new_train['navstat'] == 15) & (new_train['sog'] <= 0.1), 'navstat'] = 1

# Same for all other navstats unequal to 0, 1, 5, 8

navstat15 = new_train[new_train['navstat'].isin([15])] 



#[ 0  1  5  3  2  8 12 13  4  6 14 11  7  9]
#print(navstat15.to_string())
# Navstat 0 - under way sailing. Kan være interresant om det er flere båter som har andre NAVSTAT og må behandles på egen måte. Er det feks en type båter som bare ligger og loker til reparasjon etc. går dårlig 
# Kanskje lurt å ha med navstat som en feature siden 
# HEr er feks kordinatene helt like over tid når navstat = 1 samme med navstat = 5 
# Se på dette 
# 0	Under way using engine - Seiling 
# 1	At anchor - stand still 
# 2	Not under command 
# 3	Restricted manoeuverability 
# 4	Constrained by her draught 
# 5	Moored - stand still 
# 6	Aground 
# 7	Engaged in Fishing - vet ikke 
# 8	Under way sailing - Seiling 

                       time    cog   sog  rot  heading  navstat       etaRaw  latitude  longitude                   vesselId                    portId
4826    2024-01-01 10:55:37   24.3   0.1    0       15       15  01-03 00:01   8.83784  -79.55147   61e9f3a7b937134a3c4bfde9  61d37cff99db2ccf7339eedd
13777   2024-01-02 04:58:04  290.5   1.7    8      312        3  01-02 05:00  50.52812   -1.18022   61e9f3f3b937134a3c4bffa3  634c4de270937fc01c3a77fc
13927   2024-01-02 05:18:50  290.9   1.6  -15      309        3  01-02 05:00  50.53129   -1.19489   61e9f3f3b937134a3c4bffa3  634c4de270937fc01c3a77fc
13979   2024-01-02 05:33:45  282.9   1.9   12      311        3  01-02 05:00  50.53366   -1.20581   61e9f3f3b937134a3c4bffa3  634c4de270937fc01c3a77fc
15346   2024-01-02 07:56:17   95.9   1.7   10      152        3  01-02 05:00  50.49552   -1.14131   61e9f3f3b937134a3c4bffa3  634c4de270937fc01c3a77fc
15477   2024-01-02 08:16:50  103.7   2.0   17      162        3  01-02 05:00  50.49297   -1.12

In [25]:
# Can you return the rows where any of cog, sog or heading is negative

negative_values = new_train[(new_train['cog'] >= 360)]
print(negative_values.to_string())


Empty DataFrame
Columns: [time, cog, sog, rot, heading, navstat, etaRaw, latitude, longitude, vesselId, portId]
Index: []


In [26]:
#print unique values for navstat 
print(new_train['navstat'].unique()) 

# print entries where navstat == 7 

navstat7 = new_train[new_train['navstat'] == 7] 
print(navstat7.to_string()) 

# Can you count the number of entries distributed over the different navstats? 

navstat_counts = new_train['navstat'].value_counts() 
print(navstat_counts) 



[ 0  1  5  3  2  8 12 13  4  6 14 11  7  9]
                       time    cog   sog  rot  heading  navstat       etaRaw  latitude  longitude                  vesselId                    portId
1039516 2024-03-29 19:53:30  303.3  17.8  0.0     80.0        7  03-28 12:00  20.62352 -107.50823  61e9f419b937134a3c4c007b  61d37ab91366c3998241d9fb
navstat
0     782185
5     605831
1     130099
2       2081
8        948
6        521
4        232
3        161
11         2
12         1
13         1
14         1
7          1
9          1
Name: count, dtype: int64


In [27]:
# change the entries where navstat == 8 to have navstat == 0
# 0	Under way using engine - Seiling 
# 1	At anchor - stand still 
# 2	Not under command 
# 3	Restricted manoeuverability 
# 4	Constrained by her draught 
# 5	Moored - stand still 
# 6	Aground 
# 7	Engaged in Fishing - vet ikke 
# 8	Under way sailing - Seiling 
# 0     782185
# 5     605831
# 1     130099
# 2       2081
# 8        948
# 6        521
# 4        232
# 3        161
# 11         2
# 12         1
# 13         1
# 14         1
# 7          1
# 9          1

#new_train.loc[new_train['navstat'] == 8, 'navstat'] = 0 

# [15,11,12,13,14,7,9,6,8,2] 

for i in [15,11,12,13,14,7,9,6,2]: 
    new_train.loc[(new_train['navstat'] == i) & (new_train['sog'] > 0.1), 'navstat'] = 0 
    new_train.loc[(new_train['navstat'] == i) & (new_train['sog'] <= 0.1), 'navstat'] = 1 

navstat_counts = new_train['navstat'].value_counts() 
print(navstat_counts) 



navstat
0    784641
5    605831
1    130252
8       948
4       232
3       161
Name: count, dtype: int64


In [28]:
# Create a csv file from new_train
new_train.to_csv('new_train.csv', index=False)